In [22]:
import requests
import hashlib
import time
import pandas as pd
from pandas import json_normalize
import json

secret_token = '696a6f47212d93f88cef71238cfb3d1cd357905b3e34eabd2bbc49124553c129'

# Generate the Unix timestamp
timestamp = int(time.time())

# Construct the query string
query_string = f'time={timestamp}'

# Generate the hash
hash_string = secret_token + str(timestamp)
hash_value = hashlib.sha512(hash_string.encode()).hexdigest()

# Construct the URL with the query string and hash
url = f'https://api.fabdb.net/cards?{query_string}&hash={hash_value}'

parameters = {
    "page": 1,
    "per_page": 100
}

total_pages = 21

# Set the request headers
headers = {
    'Authorization': f'Bearer {secret_token}',
    'Accept': 'application/json'
}


In [28]:
#empty list to hold paginated data
data_records = []

for page in range(1, total_pages + 1):
    parameters['page'] = page
    
    response = requests.get(url, params=parameters)

    # process response
    data = response.json()

    print(data)

    # Extract the relevant data records from the response
    data_records.extend(data['data'])

# Normalize the data before storing it in the dataframe
df = pd.json_normalize(data_records)


{'data': [{'identifier': 'eye-of-ophidia', 'name': 'Eye of Ophidia', 'legality': [], 'keywords': ['generic', 'resource', 'gem'], 'stats': {'resource': 3}, 'text': '**Legendary** *(You may only have 1 Eye of Ophidia in your deck.)*\r\n\r\nWhen you pitch Eye of Ophidia, **opt 2**.', 'rarity': 'F', 'image': 'https://fabdb2.imgix.net/cards/printings/ARC000-CF.png?w=400&fit=clip&auto=compress,format', 'printings': [{'id': 863, 'language': 'en', 'name': 'Eye of Ophidia', 'text': '**Legendary** *(You may only have 1 Eye of Ophidia in your deck.)*\n\nWhen you pitch Eye of Ophidia, **opt 2**.', 'flavour': 'Beyond the turbulent waters of Death’s Knell, the ocean stretches as far as the eye can see, an endless, unfathomable expanse of deep blue. The keeper looks upon the shifting tides, feeling the weight of time within its weary soul. As the great divide draws near, it relinquishes a part of itself, bequeathing the gift of its immeasurable knowledge. Under the light of the pale moon, the ocean c

In [ ]:
df.rename(columns={'stats.resource': 'pitch value'}, inplace=True)

# Map the values in 'pitch value' column to corresponding colors
df['pitch value'] = df['pitch value'].map({1: 'Red', 2: 'Yellow', 3: 'Blue'})

# Rename other columns
df.rename(columns={'stats.life': 'life', 'stats.intellect': 'intellect','stats.attack': 'attack', 'stats.defense': 'defense', 'stats.cost': 'cost'}, inplace=True)
#drop stats column after it's been split
columns_to_drop = ['stats']
df.drop(columns_to_drop, axis=1, inplace=True)


In [ ]:
# converting select columns to numeric for statistical analysis
columns_to_convert = ['life', 'attack', 'defense', 'cost', 'intellect']
df[columns_to_convert] = df[columns_to_convert].apply(pd.to_numeric, errors='coerce', downcast='float')
pd.set_option('display.max_rows', None)  # Show all rows
df.head(4)

identifier                           name legality  \
0                eye-of-ophidia                 Eye of Ophidia       []   
1  dash-inventor-extraordinaire  Dash, Inventor Extraordinaire       []   
2                          dash                           Dash       []   
3           teklo-plasma-pistol            Teklo Plasma Pistol       []   

                              keywords  \
0             [generic, resource, gem]   
1                [mechanologist, hero]   
2         [mechanologist, hero, young]   
3  [mechanologist, weapon, pistol, 2h]   

                                                text rarity  \
0  **Legendary** *(You may only have 1 Eye of Oph...      F   
1  You may start the game with a Mechanologist it...      T   
2  You may start the game with a Mechanologist it...      T   
3  **Action** - Remove a steam counter from Teklo...      T   

                                               image  \
0  https://fabdb2.imgix.net/cards/printings/ARC00...   
1  https://fabdb2.imgix.net/cards/printings/ARC00...   
2  https://fabdb2.imgix.net/cards/printings/ARC00...   
3  https://fabdb2.imgix.net/cards/printings/ARC00...   

                                           printings pitch value  life  \
0  [{'id': 863, 'language': 'en', 'name': 'Eye of...        Blue   NaN   
1  [{'id': 864, 'language': 'en', 'name': 'Dash, ...         NaN  40.0   
2  [{'id': 865, 'language': 'en', 'name': 'Dash',...         NaN  20.0   
3  [{'id': 866, 'language': 'en', 'name': 'Teklo ...         NaN   NaN   

   intellect  attack  defense  cost  
0        NaN     NaN      NaN   NaN  
1        4.0     NaN      NaN   NaN  
2        4.0     NaN      NaN   NaN  
3        NaN     2.0      NaN   NaN